# Account Management 101

In [2]:
import geodesic

### Your Account

When you access Geodesic, the API reaches out to an external identity provider to get a token to interact with the backend. 
That token carries some information about you and your current permissions level, but also we have a backend service that
adds to and customizes that information. You can get your user profile using the built-in `myself` function

In [5]:
u = geodesic.myself()
dict(u)

{'subject': 'auth0|611c3d206a08f0006c8a9290',
 'first_name': '',
 'last_name': '',
 'middle_name': '',
 'alias': 'gcp-headless@seerai.space',
 'email': 'gcp-headless@seerai.space',
 'avatar': 'https://s.gravatar.com/avatar/ff1b38649bdb3d54918f07a81ba0b036?s=480&r=pg&d=https%3A%2F%2Fcdn.auth0.com%2Favatars%2Fgc.png',
 'pronouns': '',
 'bio': ''}

As you can see, this carries information about you, or in this case, our service account user. You can edit all of this information directly

In [6]:
u.first_name = "Geodesic"
u.middle_name = "API"
u.last_name = "User"
u.alias = "Headless User"
u.pronouns = "it/its"
u.bio = "I'm a robot that manages some internal stuff for SeerAI. Will you be my friend?"

u.save()

In [7]:
dict(u)

{'subject': 'auth0|611c3d206a08f0006c8a9290',
 'first_name': 'Geodesic',
 'last_name': 'User',
 'middle_name': 'API',
 'alias': 'Headless User',
 'email': 'gcp-headless@seerai.space',
 'avatar': 'https://s.gravatar.com/avatar/ff1b38649bdb3d54918f07a81ba0b036?s=480&r=pg&d=https%3A%2F%2Fcdn.auth0.com%2Favatars%2Fgc.png',
 'pronouns': 'it/its',
 'bio': "I'm a robot that manages some internal stuff for SeerAI. Will you be my friend?"}

You can check permissions and roles

In [8]:
print(f'permissions = {u.get_permissions}, roles = {u.get_roles}')

permissions = ['spacetime:read', 'spacetime:write', 'tesseract:read', 'tesseract:write', 'entanglement:read', 'entanglement:write'], roles = ['user']


You are uniquely identified in the system by the `subject` field. This is a unique string provided by your identity provider. We'll get into resource sharing in a second, but the `subject` is always used as that unique identifier for a user within the platform.

### Projects

Perhaps the most important part of Geodesic is a `Project`. `Projects` are like your personal work area within the SeerAI Graph. You can store datasets and other objects and connections here and they will only be visible to those that you share them with. You can list `Projects` that you can access using the `get_projects` function.

In [11]:
geodesic.get_projects()

[{'name': 'global',
  'alias': 'Global Graph',
  'description': 'The Global Project. All can read, few can write.',
  'owner': '',
  'keywords': 'global',
  'uid': 'global'}]

Create a new `Project` with the `create_project` function

In [12]:
p = geodesic.create_project(name="docs-example", alias="Docs Example Project", description="Test project for illustration purposes")
p

{'name': 'docs-example',
 'alias': 'Docs Example Project',
 'description': 'Test project for illustration purposes',
 'keywords': '',
 'uid': 'b96a3c8f8104b671d19ff7dbad5b7026992d7643',
 'owner': 'auth0|611c3d206a08f0006c8a9290'}

your `active_project` is where everything you do will get saved by default (anything that writes to the backend). You can see your `active project` with the `get_active_project` function. It always defaults to *global*, but can be changed at runtime.

In [13]:
geodesic.get_active_project()

{'name': 'global',
 'alias': 'Global Graph',
 'description': 'The Global Project. All can read, few can write.',
 'owner': '',
 'keywords': 'global',
 'uid': 'global'}

In [14]:
geodesic.set_active_project(p)

{'name': 'docs-example',
 'alias': 'Docs Example Project',
 'description': 'Test project for illustration purposes',
 'keywords': '',
 'uid': 'b96a3c8f8104b671d19ff7dbad5b7026992d7643',
 'owner': 'auth0|611c3d206a08f0006c8a9290'}

In [15]:
geodesic.get_active_project()

{'name': 'docs-example',
 'alias': 'Docs Example Project',
 'description': 'Test project for illustration purposes',
 'keywords': '',
 'uid': 'b96a3c8f8104b671d19ff7dbad5b7026992d7643',
 'owner': 'auth0|611c3d206a08f0006c8a9290'}

Most users do not have write access to global, but everyone can read from it. This is the currated graph, and should be protected. Even though the whole system is version controlled, too many people editing *global* would end up with a messy knowledge graph.

### Credentials

Credentials allow a user to let Geodesic access some secure resource on their behalf. That is things like APIs and Cloud Storage like S3, Azure Blob Storage, and Google Cloud Storage. Any user can add credentials, and they are stored internally in an encrypted format. They can never be read back by any user, including an admin. Once they are there, only certain internal services are able to retrieve the encrypted credentials for exhange with an API that a user has authorized for access.

Imagine I need to provide access to imagery stored in an S3 bucket. In that case, I need to create a `Credential` object

In [17]:
from geodesic.account import Credential, get_credential, get_credentials, valid_types

In [18]:
valid_types

['SERVICE_ACCOUNT_KEY',
 'AWS_KEY_PAIR',
 'AZURE_ACCESS_KEY',
 'JWT',
 'OAUTH2_CLIENT_CREDENTIALS',
 'OAUTH2_REFRESH_TOKEN',
 'BASIC_AUTH']

In [23]:
c = Credential(name="s3-bucket", type='AWS_KEY_PAIR', data={
    'aws_secret_access_key': "mysecretaccesskey",
    'aws_access_key_id': "myaccesskeyid"
})
c.create()

Credentials can be referred to by their `uid` (autogenerated) or `name`. 